<P><strong> <span style="color: rgb(192, 68, 238);font-size: 26px;"> PCI Planning based on DOCPLEX </strong></p>

<p><span style="color: rgb(83, 77, 243);"> In this notebook we solve the optimization problem by using DOCPLEX package. Our method assigns a PCI value to each site, and finds the PCI values of the sectors of each site. If PCI value e is assigned to site n, pci of sector 0 of site n is 3e, pci of sector 1 of site n is 3e+1 and pci of sector 2 of site n is 3e+2.
    </span></p>

In [1]:
import pandas as pd
import numpy as np
from matplotlib import pyplot as plt
from itertools import product
import random
import sys
np.set_printoptions(threshold=sys.maxsize)
import docplex.mp
import cplex
from numpy import savetxt
from numpy import loadtxt
import time
from colorama import Fore
from docplex.mp.model import Model

import plotly.express as px
import plotly.graph_objects as go
import plotly.io as pio
pio.renderers.default='notebook'

pd.options.plotting.backend = "plotly"

<p><span style="color: rgb(83, 77, 243);"> Let's load the power matrix.
    </span></p>

In [26]:
power_matrix = loadtxt('random_example_1_power_matrix.csv', delimiter=',')

In [27]:
power_matrix.shape

(99, 78)

<p><span style="color: rgb(83, 77, 243);"> The following matrix, power_matrix_diff is composed of elements of power_matrix. This matrix contains the ratio of the received powers from sectors around a grid center. To be more precise, for each grid center g, and two sectors i and j that transmit nonzero powers p_i and p_j to g, the element (g,i,j) of power_matrix_diff is min(p_i,p_j)/max(p_i,p_j). 
    </span></p>

<P><strong> <span style="color: rgb(24, 230, 245);font-size: 20px;"> Parameters </strong></p>

<p><span style="color: rgb(83, 77, 243);"> We define the parameters of our algorithm.
    </span></p>

In [28]:
grid_count = power_matrix.shape[0]
site_count = int(power_matrix.shape[1]/3)
site_sector_count = int(site_count*3)
pci_max_third = 3  # pci_max = 3*3+2 = 11
pci_max = pci_max_third*3 + 2

w1 = 8
w2 = 2

<p><span style="color: rgb(83, 77, 243);"> PCI vector is a vector that contains possible PCI vlaues. It is equivalent to L in problem formulation document.
    </span></p>

In [29]:
pci_vector = np.array(range(pci_max))

In [30]:
pci_vector.shape

(11,)

<p><span style="color: rgb(83, 77, 243);"> Mode matrix is M in problem formulation document.
    </span></p>

In [31]:
mode_matrix = np.zeros(shape=(pci_max,3))
for pci in pci_vector:
    mode_matrix[pci,pci%3] = 1

In [32]:
print(mode_matrix)

[[1. 0. 0.]
 [0. 1. 0.]
 [0. 0. 1.]
 [1. 0. 0.]
 [0. 1. 0.]
 [0. 0. 1.]
 [1. 0. 0.]
 [0. 1. 0.]
 [0. 0. 1.]
 [1. 0. 0.]
 [0. 1. 0.]]


<P><strong> <span style="color: rgb(24, 230, 245);font-size: 20px;"> Functions </strong></p>

<p><span style="color: rgb(83, 77, 243);"> We can address sectors by an integer or with a tuple. Sector (n,i) is equivalent to sector 3n+i. The following functions convert these two notations.
    </span></p>

In [33]:
def site_sector_int_to_tuple(site_sector):
    if site_sector % 3 == 0:
        return int(site_sector/3),0
    elif site_sector % 3 ==1 :
        return int((site_sector-1)/3), 1
    elif site_sector % 3 ==2 :
        return int((site_sector-2)/3), 2
        
def site_sector_tuple_to_int(tuple_):
    return tuple_[0]*3 + tuple_[1]

<p><span style="color: rgb(83, 77, 243);"> The following function prints the PCI values of sectors based on the allocation matrix. </span></p>

In [34]:
def translate_allocation(local_allocation_matrix):
    for i in range(local_allocation_matrix.shape[0]):
        for j in range(local_allocation_matrix.shape[1]):
            if local_allocation_matrix[i,j] != 0:
                print('{} ===> {}'.format(site_sector_int_to_tuple(i), j+1))

<p><span style="color: rgb(83, 77, 243);"> The following function indicates the number of the same PCI sectors that transmit signal on a grid center. It returns a vector whose length is the number of grid centers.
    </span></p>

In [35]:
def get_collisions(local_allocation_matrix, indicator_power_matrix_diff):
    
    n_grid = indicator_power_matrix_diff.shape[0]
    grid_collisions= np.zeros(n_grid)
    for grid in range(grid_count):
        grid_collisions[grid] = np.trace(np.matmul(np.matmul(np.transpose(local_allocation_matrix), 
                                                             indicator_power_matrix_diff[grid,:,:]),
                                                               local_allocation_matrix)) 
    return grid_collisions

<p><span style="color: rgb(83, 77, 243);"> The following function indicates the number of same PCI mod 3 sectors that transmit signal on a grid center. It returns a vector whose length is the number of grid centers.
    </span></p>

In [36]:
def get_collisions_mod3(local_allocation_matrix, indicator_power_matrix_diff):
    
    n_grid = indicator_power_matrix_diff.shape[0]
    grid_collisions= np.zeros(n_grid)
    for grid in range(grid_count):
        grid_collisions[grid] = np.trace(np.matmul(np.matmul(np.matmul(np.matmul(np.transpose(mode_matrix),
                                                                                 np.transpose(local_allocation_matrix)),
                                                                       indicator_power_matrix_diff[grid,:,:]),
                                                            local_allocation_matrix),
                                                   mode_matrix))
    return grid_collisions

<P><strong> <span style="color: rgb(24, 230, 245);font-size: 20px;"> Back to Power Matrix </strong></p>

In [37]:
power_matrix_diff = np.zeros(shape=(grid_count,site_sector_count,site_sector_count),dtype='float16')

for grid in range(grid_count):
    for i in range(site_sector_count):
        for j in range(site_sector_count):
            if i == j:
                power_matrix_diff[grid,i,j] = 10  # to make it psd
            else:        
                if power_matrix[grid,i] == 0 or power_matrix[grid,j] == 0:   # this subtle condition is important
                    power_matrix_diff[grid,i,j] = 0
                else:
                    power_matrix_diff[grid,i,j] = min(power_matrix[grid,i]/power_matrix[grid,j],power_matrix[grid,j]/power_matrix[grid,i])

<p><span style="color: rgb(83, 77, 243);">
    Normally, the diagonal of power_matrix_diff should be zero, because only one power from each sector is received at each grid center, and there is no need for ratio. However, adding a great enough constant to diagonal of power_matrix_diff makes
    it PSD (positive semi definite), and only adds a constant to objective function, so it does not affect the optimization.
 </span></p> 

In [38]:
# memory size of power_matrix_diff in bytes:
# power_matrix_diff.nbytes
# power_matrix_diff.size * power_matrix_diff.itemsize
power_matrix_diff

array([[[1.0000e+01, 0.0000e+00, 0.0000e+00, 0.0000e+00, 0.0000e+00,
         0.0000e+00, 0.0000e+00, 0.0000e+00, 0.0000e+00, 0.0000e+00,
         0.0000e+00, 0.0000e+00, 0.0000e+00, 0.0000e+00, 0.0000e+00,
         0.0000e+00, 0.0000e+00, 0.0000e+00, 0.0000e+00, 0.0000e+00,
         0.0000e+00, 0.0000e+00, 0.0000e+00, 0.0000e+00, 0.0000e+00,
         0.0000e+00, 0.0000e+00, 0.0000e+00, 0.0000e+00, 0.0000e+00,
         0.0000e+00, 0.0000e+00, 0.0000e+00, 0.0000e+00, 0.0000e+00,
         0.0000e+00, 0.0000e+00, 0.0000e+00, 0.0000e+00, 0.0000e+00,
         0.0000e+00, 0.0000e+00, 0.0000e+00, 0.0000e+00, 0.0000e+00,
         0.0000e+00, 0.0000e+00, 0.0000e+00, 0.0000e+00, 0.0000e+00,
         0.0000e+00, 0.0000e+00, 0.0000e+00, 0.0000e+00, 0.0000e+00,
         0.0000e+00, 0.0000e+00, 0.0000e+00, 0.0000e+00, 0.0000e+00,
         0.0000e+00, 0.0000e+00, 0.0000e+00, 0.0000e+00, 0.0000e+00,
         0.0000e+00, 0.0000e+00, 0.0000e+00, 0.0000e+00, 0.0000e+00,
         0.0000e+00, 0.0000e+00, 0

In [39]:
power_matrix_diff.size

602316

In [40]:
power_matrix_diff.itemsize

2

<p><span style="color: rgb(83, 77, 243);">
 We can check the correctness of power_matrix_diff by checking the indices of its nonzero elements. 
 </span></p> 

In [41]:
power_matrix_diff_nonzero = np.nonzero(power_matrix_diff)

for i in range(len(power_matrix_diff_nonzero[0])):
    # do not print diagonal:
    if site_sector_int_to_tuple(power_matrix_diff_nonzero[1][i]) != site_sector_int_to_tuple(power_matrix_diff_nonzero[2][i]):
        print((power_matrix_diff_nonzero[0][i],site_sector_int_to_tuple(power_matrix_diff_nonzero[1][i]),
           site_sector_int_to_tuple(power_matrix_diff_nonzero[2][i])))

(2, (4, 2), (20, 2))
(2, (20, 2), (4, 2))
(4, (8, 2), (22, 2))
(4, (22, 2), (8, 2))
(5, (16, 2), (18, 2))
(5, (16, 2), (22, 2))
(5, (18, 2), (16, 2))
(5, (18, 2), (22, 2))
(5, (22, 2), (16, 2))
(5, (22, 2), (18, 2))
(6, (2, 2), (21, 2))
(6, (21, 2), (2, 2))
(7, (21, 2), (24, 2))
(7, (24, 2), (21, 2))
(13, (4, 2), (5, 2))
(13, (4, 2), (9, 2))
(13, (4, 2), (13, 2))
(13, (4, 2), (20, 2))
(13, (5, 2), (4, 2))
(13, (5, 2), (9, 2))
(13, (5, 2), (13, 2))
(13, (5, 2), (20, 2))
(13, (9, 2), (4, 2))
(13, (9, 2), (5, 2))
(13, (9, 2), (13, 2))
(13, (9, 2), (20, 2))
(13, (13, 2), (4, 2))
(13, (13, 2), (5, 2))
(13, (13, 2), (9, 2))
(13, (13, 2), (20, 2))
(13, (20, 2), (4, 2))
(13, (20, 2), (5, 2))
(13, (20, 2), (9, 2))
(13, (20, 2), (13, 2))
(14, (9, 2), (13, 2))
(14, (13, 2), (9, 2))
(15, (6, 1), (16, 1))
(15, (6, 1), (22, 2))
(15, (16, 1), (6, 1))
(15, (16, 1), (22, 2))
(15, (22, 2), (6, 1))
(15, (22, 2), (16, 1))
(16, (6, 1), (16, 1))
(16, (6, 1), (18, 2))
(16, (16, 1), (6, 1))
(16, (16, 1), (18,

<p><span style="color: rgb(83, 77, 243);">
    The following matrix, indicator_power_matrix is the same size as power_matrix_diff. The equivalent of 0 elements of power_matrix_diff is also 0 in indicator_power_matrix. The equivalent of nonzero elements of power_matrix_diff is 1 in indicator_power_matrix. 
 </span></p> 

In [42]:
indicator_power_matrix_diff = np.zeros(shape=(grid_count,site_sector_count,site_sector_count),dtype='int8')

for grid in range(grid_count):
    for i in range(site_sector_count):
        for j in range(site_sector_count):
            if i==j or power_matrix[grid,i] == 0 or power_matrix[grid,j] == 0:
                indicator_power_matrix_diff[grid,i,j] = 0
            else:
                indicator_power_matrix_diff[grid,i,j] = 1

<P><strong> <span style="color: rgb(24, 230, 245);font-size: 20px;"> Optimzation (DOCPLEX) </strong></p>

<p><span style="color: rgb(83, 77, 243);"> We calculate the time taken by DOCPLEX to solve the problem.
    </span></p>

In [43]:
start_time = time.time()

<p><span style="color: rgb(83, 77, 243);"> model definition
    </span></p>

In [44]:
mdl = Model(name="PCI")

<p><span style="color: rgb(83, 77, 243);"> Now we define the allocation matrix variable X which is a matrix of binary elements. This matrix allocates PCI values to sites (not sectors) and each row of X is dedicated to a site. If i'th elelement in row n is 1, then PCI value of site n is i.
    </span></p>

In [45]:
X = mdl.binary_var_matrix(site_count,pci_max_third, name=lambda ij: "X_%d_%d" %(ij[0], ij[1]))

<p><span style="color: rgb(83, 77, 243);">
 Each site can have only one PCI value, so the sum of elements in each row of X should be 1.
 </span></p> 

In [46]:
# Condition for each row of X to sum to 1
mdl.add_constraints(mdl.sum(X[i,j] for j in range(pci_max_third)) == 1 for i in range(site_count))

[docplex.mp.LinearConstraint[](X_0_0+X_0_1+X_0_2,EQ,1),
 docplex.mp.LinearConstraint[](X_1_0+X_1_1+X_1_2,EQ,1),
 docplex.mp.LinearConstraint[](X_2_0+X_2_1+X_2_2,EQ,1),
 docplex.mp.LinearConstraint[](X_3_0+X_3_1+X_3_2,EQ,1),
 docplex.mp.LinearConstraint[](X_4_0+X_4_1+X_4_2,EQ,1),
 docplex.mp.LinearConstraint[](X_5_0+X_5_1+X_5_2,EQ,1),
 docplex.mp.LinearConstraint[](X_6_0+X_6_1+X_6_2,EQ,1),
 docplex.mp.LinearConstraint[](X_7_0+X_7_1+X_7_2,EQ,1),
 docplex.mp.LinearConstraint[](X_8_0+X_8_1+X_8_2,EQ,1),
 docplex.mp.LinearConstraint[](X_9_0+X_9_1+X_9_2,EQ,1),
 docplex.mp.LinearConstraint[](X_10_0+X_10_1+X_10_2,EQ,1),
 docplex.mp.LinearConstraint[](X_11_0+X_11_1+X_11_2,EQ,1),
 docplex.mp.LinearConstraint[](X_12_0+X_12_1+X_12_2,EQ,1),
 docplex.mp.LinearConstraint[](X_13_0+X_13_1+X_13_2,EQ,1),
 docplex.mp.LinearConstraint[](X_14_0+X_14_1+X_14_2,EQ,1),
 docplex.mp.LinearConstraint[](X_15_0+X_15_1+X_15_2,EQ,1),
 docplex.mp.LinearConstraint[](X_16_0+X_16_1+X_16_2,EQ,1),
 docplex.mp.LinearConstrain

<p><span style="color: rgb(83, 77, 243);">
 Now we define another allocation matrix Y wich is also binary, but allocates PCI values to sectors and is completely composed of X. Each row n of X generates 3 rows in Y, one for each sector of site n. If matrix X assignes PCI value 'e' to site n, matrix Y assings 3e to sector 0 of site n, 3e+1 to sector 1, and 3e+2 to sector 2.
 </span></p> 

In [47]:
Y = mdl.binary_var_matrix(site_sector_count,pci_max, name=lambda ij: "Y_%d_%d" %(ij[0], ij[1]))

for i in range(site_sector_count):
    for j in range(pci_max_third):
        if i%3 == 0:
            mdl.add_constraint(Y[i,3*j] == X[i//3,j])
            mdl.add_constraint(Y[i,3*j+1] == 0)
            mdl.add_constraint(Y[i,3*j+2] == 0)
        elif i%3 == 1:
            mdl.add_constraint(Y[i,3*j] == 0)
            mdl.add_constraint(Y[i,3*j+1] == X[(i-1)//3,j])
            mdl.add_constraint(Y[i,3*j+2] == 0)
        elif i%3 == 2:
            mdl.add_constraint(Y[i,3*j] == 0)
            mdl.add_constraint(Y[i,3*j+1] == 0)
            mdl.add_constraint(Y[i,3*j+2] == X[(i-2)//3,j])

<p><span style="color: rgb(83, 77, 243);">
Now we define the objective function.
 </span></p> 

In [48]:
obj1 = w1*mdl.sum(Y[i,k]*Y[j,k]*power_matrix_diff[g,i,j] 
             for i in range(site_sector_count) for j in range(site_sector_count) for k in range(pci_max) for g in range(grid_count))

obj2 = w2*mdl.sum(mdl.sum(Y[i,z]*mode_matrix[z,h] for z in range(pci_max))*
                  mdl.sum(Y[j,z]*mode_matrix[z,h] for z in range(pci_max))*
                  power_matrix_diff[g,i,j]
                  for h in range(3)
                  for i in range(site_sector_count)
                  for j in range(site_sector_count)
                  for g in range(grid_count))

<p><span style="color: rgb(83, 77, 243);">
We want to minimize the objective.
 </span></p> 

In [49]:
mdl.minimize(obj1+obj2)

<p><span style="color: rgb(83, 77, 243);">
We can see the number of variables and constraints of the model.
 </span></p> 

In [50]:
mdl.print_information()

Model: PCI
 - number of variables: 936
   - binary=936, integer=0, continuous=0
 - number of constraints: 728
   - linear=728
 - parameters: defaults
 - objective: minimize quadratic
 - problem type is: MIQP


<p><span style="color: rgb(83, 77, 243);">
 Finally we can solve the model 😊
 </span></p> 

In [51]:
mdl.solve()

docplex.mp.solution.SolveSolution(obj=772443,values={X_0_2:1,X_1_0:1,X_2..

In [52]:
end_time = time.time()
elapsed_time = end_time - start_time

In [54]:
print(Fore.MAGENTA + 'elapsed time: {} s'.format(round(elapsed_time,2)))

elapsed time: 298.63 s


<p><span style="color: rgb(83, 77, 243);">
 Now we form the allocation matrix solution, cplex_allocation_matrix, from matrix Y.
 </span></p> 

In [55]:
cplex_allocation_matrix = np.zeros((site_sector_count,pci_max))
for i in range(site_sector_count):
    for j in range(pci_max):
        cplex_allocation_matrix[i,j] = Y[i,j].solution_value

<p><span style="color: rgb(83, 77, 243);">
The matrix cplex_sub_allocation_matrix contains the solution for X (PCI values of sites).
 </span></p> 

In [56]:
cplex_sub_allocation_matrix = np.zeros((site_count,pci_max_third))
for i in range(site_count):
    for j in range(pci_max_third):
        cplex_sub_allocation_matrix[i,j] = X[i,j].solution_value

<p><span style="color: rgb(83, 77, 243);">
Saving the results:
 </span></p> 

In [57]:
savetxt('random_example_1_docplex_solution.csv', cplex_allocation_matrix, delimiter=',')

In [58]:
cplex_allocation_matrix

array([[0., 0., 0., 0., 0., 0., 1., 0., 0., 0., 0.],
       [0., 0., 0., 0., 0., 0., 0., 1., 0., 0., 0.],
       [0., 0., 0., 0., 0., 0., 0., 0., 1., 0., 0.],
       [1., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0.],
       [0., 1., 0., 0., 0., 0., 0., 0., 0., 0., 0.],
       [0., 0., 1., 0., 0., 0., 0., 0., 0., 0., 0.],
       [0., 0., 0., 0., 0., 0., 1., 0., 0., 0., 0.],
       [0., 0., 0., 0., 0., 0., 0., 1., 0., 0., 0.],
       [0., 0., 0., 0., 0., 0., 0., 0., 1., 0., 0.],
       [0., 0., 0., 0., 0., 0., 1., 0., 0., 0., 0.],
       [0., 0., 0., 0., 0., 0., 0., 1., 0., 0., 0.],
       [0., 0., 0., 0., 0., 0., 0., 0., 1., 0., 0.],
       [0., 0., 0., 0., 0., 0., 1., 0., 0., 0., 0.],
       [0., 0., 0., 0., 0., 0., 0., 1., 0., 0., 0.],
       [0., 0., 0., 0., 0., 0., 0., 0., 1., 0., 0.],
       [0., 0., 0., 1., 0., 0., 0., 0., 0., 0., 0.],
       [0., 0., 0., 0., 1., 0., 0., 0., 0., 0., 0.],
       [0., 0., 0., 0., 0., 1., 0., 0., 0., 0., 0.],
       [1., 0., 0., 0., 0., 0., 0., 0., 0., 0.

In [59]:
cplex_sub_allocation_matrix

array([[0., 0., 1.],
       [1., 0., 0.],
       [0., 0., 1.],
       [0., 0., 1.],
       [0., 0., 1.],
       [0., 1., 0.],
       [1., 0., 0.],
       [0., 1., 0.],
       [1., 0., 0.],
       [1., 0., 0.],
       [0., 0., 1.],
       [1., 0., 0.],
       [1., 0., 0.],
       [0., 0., 1.],
       [1., 0., 0.],
       [1., 0., 0.],
       [0., 0., 1.],
       [0., 1., 0.],
       [1., 0., 0.],
       [0., 1., 0.],
       [0., 1., 0.],
       [1., 0., 0.],
       [0., 1., 0.],
       [0., 0., 1.],
       [0., 1., 0.],
       [1., 0., 0.]])

In [ ]:
# translate_allocation(cplex_allocation_matrix)

In [60]:
mdl.objective_value

772442.8594207764

<p><span style="color: rgb(83, 77, 243);">
Lets see the number of collisions and collisions mod 3. Collisions is the number of grid centers that receive signal from two or more same PCI sectors. Collisions mod 3 is the number of grid centers that receive signal from two or more same PCI mod 3 sectors. 
 </span></p> 

In [61]:
cplex_colisions = get_collisions(cplex_allocation_matrix, indicator_power_matrix_diff)
cplex_colisions_mod3 = get_collisions_mod3(cplex_allocation_matrix, indicator_power_matrix_diff)

In [62]:
cplex_colisions.shape

(99,)

In [63]:
cplex_colisions

array([0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 4., 0., 0., 0.,
       0., 0., 0., 0., 0., 0., 0., 0., 0., 2., 0., 0., 0., 0., 0., 0., 0.,
       0., 0., 2., 0., 2., 0., 0., 0., 0., 0., 0., 0., 2., 0., 4., 0., 0.,
       0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0.,
       0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0.,
       0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0.])

In [64]:
for i in range(len(cplex_colisions)):
    if cplex_colisions[i] >0:
        print("grid {} has {} collisions.".format(i,cplex_colisions[i]))

grid 13 has 4.0 collisions.
grid 26 has 2.0 collisions.
grid 36 has 2.0 collisions.
grid 38 has 2.0 collisions.
grid 46 has 2.0 collisions.
grid 48 has 4.0 collisions.


In [65]:
for i in range(len(cplex_colisions_mod3)):
    if cplex_colisions_mod3[i] >0:
        print("grid {} has {} collisions.".format(i,cplex_colisions_mod3[i]))

grid 2 has 2.0 collisions.
grid 4 has 2.0 collisions.
grid 5 has 6.0 collisions.
grid 6 has 2.0 collisions.
grid 7 has 2.0 collisions.
grid 13 has 20.0 collisions.
grid 14 has 2.0 collisions.
grid 15 has 2.0 collisions.
grid 16 has 2.0 collisions.
grid 17 has 4.0 collisions.
grid 18 has 2.0 collisions.
grid 22 has 2.0 collisions.
grid 25 has 2.0 collisions.
grid 26 has 6.0 collisions.
grid 28 has 2.0 collisions.
grid 29 has 2.0 collisions.
grid 30 has 2.0 collisions.
grid 33 has 2.0 collisions.
grid 34 has 2.0 collisions.
grid 35 has 2.0 collisions.
grid 36 has 10.0 collisions.
grid 37 has 4.0 collisions.
grid 38 has 6.0 collisions.
grid 39 has 12.0 collisions.
grid 40 has 2.0 collisions.
grid 41 has 6.0 collisions.
grid 44 has 2.0 collisions.
grid 45 has 2.0 collisions.
grid 46 has 14.0 collisions.
grid 48 has 20.0 collisions.
grid 49 has 8.0 collisions.
grid 51 has 2.0 collisions.
grid 52 has 6.0 collisions.
grid 55 has 6.0 collisions.
grid 56 has 2.0 collisions.
grid 57 has 4.0 coll